In [1]:
# Notebook parameters. Values here are for development only and 
# will be overridden when running via snakemake and papermill.
cohort_id = "CD-NU_Gbadolite_gamb_2015_Q3"
# cohort_id = 'ML-2_Kati_colu_2014_Q3'
# cohort_id = 'CI-LG_Agneby-Tiassa_colu_2012'
cohorts_analysis = "20230223"
contigs = ['2RL', '3RL', 'X']
sample_sets = "3.0"
min_cohort_size = 20
max_cohort_size = 50
h12_calibration_contig = '3L'
use_gcs_cache = False
dask_scheduler = "threads"

In [2]:
# Parameters
min_cohort_size = 20
max_cohort_size = 50
sample_sets = ["3.0"]
contigs = ["2RL", "3RL", "X"]
cohorts_analysis = "20230223"
h12_calibration_contig = "3L"
h12_signal_detection_min_delta_aic = 1000
h12_signal_detection_min_stat_max = 0.1
h12_signal_detection_gflanks = [6]
use_gcs_cache = False
dask_scheduler = "single-threaded"
cohort_id = "GM-N_Central-Baddibu_gcx1_2011_Q3"


In [3]:
from IPython.display import Markdown, HTML
import malariagen_data
import numpy as np
import pandas as pd
from pyprojroot import here
import yaml
import dask
dask.config.set(scheduler=dask_scheduler);
from textwrap import dedent

import geopandas as gpd
import bokeh.layouts as bklay
import bokeh.plotting as bkplt
import bokeh.models as bkmod
import plotly.express as px

from bokeh.io import output_notebook # enables plot interface in J notebook

# N.B., do not add the "remove-output" tag to this cell!!! If you do,
# the bokeh javascript libraries will not get loaded in the generated
# HTML page. The call to output_notebook() injects javascript in the
# cell output which triggers the bokeh javascript libraries to be loaded
# in the page.
output_notebook(hide_banner=True)

# Gambia, The / Central Baddibu / gcx1 / 2011 / Q3

In [4]:
# Load cohorts to find sample query to select samples for this cohort.

df_cohorts = gpd.read_file(here() / "build" / "final_cohorts.geojson").set_index("cohort_id")
cohort = df_cohorts.loc[cohort_id]
cohort

cohort_size                                                          52
country                                                     Gambia, The
admin1_iso                                                         GM-N
admin1_name                                                     Kerewan
admin2_name                                              Central Badibu
taxon                                                              gcx1
year                                                               2011
quarter                                                               3
cohort_label           Gambia, The / Central Baddibu / gcx1 / 2011 / Q3
sample_query          cohort_admin2_quarter == 'GM-N_Central-Baddibu...
latitude                                                          13.55
longitude                                                         -15.9
h12_window_size                                                  1000.0
country_alpha2                                                  

In [5]:
# Initialise access to MalariaGEN data.

extra_params = dict()
if use_gcs_cache:
    extra_params["url"] = "simplecache::gs://vo_agam_release"
    extra_params["simplecache"] = dict(cache_storage=(here() / "gcs_cache").as_posix())

ag3 = malariagen_data.Ag3(
    # Pin the version of the cohorts analysis for reproducibility.
    cohorts_analysis=cohorts_analysis,
    results_cache=(here() / "malariagen_data_cache").as_posix(),
    **extra_params,
)
ag3

<MalariaGEN Ag3 API client>
Storage URL             : gs://vo_agam_release/
Data releases available : 3.0, 3.1, 3.2, 3.3, 3.4, 3.5, 3.6, 3.7, 3.8
Results cache           : /home/sanjaynagi/selection-atlas/malariagen_data_cache
Cohorts analysis        : 20230223
AIM analysis            : 20220528
Site filters analysis   : dt_20200416
Software version        : malariagen_data 7.13.0
Client location         : unknown
---
Please note that data are subject to terms of use,
for more information see https://www.malariagen.net/data
or contact data@malariagen.net. For API documentation see 
https://malariagen.github.io/vector-data/ag3/api.html

In [6]:
# Load sample metadata for this cohort.

df_samples = ag3.sample_metadata(sample_query=cohort['sample_query'])
df_samples

sample_id partner_sample_id      contributor      country    location  \
0   AG0147-C              2614  Martin Donnelly  Gambia, The  Njabakunda   
1   AG0159-C              2626  Martin Donnelly  Gambia, The  Njabakunda   
2   AG0129-C              2596  Martin Donnelly  Gambia, The  Njabakunda   
3   AG0153-C              2620  Martin Donnelly  Gambia, The  Njabakunda   
4   AG0163-C              2630  Martin Donnelly  Gambia, The  Njabakunda   
5   AG0098-C              2534  Martin Donnelly  Gambia, The  Njabakunda   
6   AG0104-C              2540  Martin Donnelly  Gambia, The  Njabakunda   
7   AG0106-C              2542  Martin Donnelly  Gambia, The  Njabakunda   
8   AG0120-C              2556  Martin Donnelly  Gambia, The  Njabakunda   
9   AG0136-C              2603  Martin Donnelly  Gambia, The  Njabakunda   
10  AG0141-C              2608  Martin Donnelly  Gambia, The  Njabakunda   
11  AG0145-C              2612  Martin Donnelly  Gambia, The  Njabakunda   
12  AG0148-C              2615  Martin Donnelly  Gambia, The  Njabakunda   
13  AG0172-C              2639  Martin Donnelly  Gambia, The  Njabakunda   
14  AG0179-C              2677  Martin Donnelly  Gambia, The  Njabakunda   
15  AG0118-C              2554  Martin Donnelly  Gambia, The  Njabakunda   
16  AG0119-C              2555  Martin Donnelly  Gambia, The  Njabakunda   
17  AG0121-C              2557  Martin Donnelly  Gambia, The  Njabakunda   
18  AG0133-C              2600  Martin Donnelly  Gambia, The  Njabakunda   
19  AG0134-C              2601  Martin Donnelly  Gambia, The  Njabakunda   
20  AG0138-C              2605  Martin Donnelly  Gambia, The  Njabakunda   
21  AG0102-C              2538  Martin Donnelly  Gambia, The  Njabakunda   
22  AG0108-C              2544  Martin Donnelly  Gambia, The  Njabakunda   
23  AG0123-C              2559  Martin Donnelly  Gambia, The  Njabakunda   
24  AG0128-C              2595  Martin Donnelly  Gambia, The  Njabakunda   
25  AG0137-C              2604  Martin Donnelly  Gambia, The  Njabakunda   
26  AG0139-C              2606  Martin Donnelly  Gambia, The  Njabakunda   
27  AG0143-C              2610  Martin Donnelly  Gambia, The  Njabakunda   
28  AG0162-C              2629  Martin Donnelly  Gambia, The  Njabakunda   
29  AG0170-C              2637  Martin Donnelly  Gambia, The  Njabakunda   
30  AG0181-C              2679  Martin Donnelly  Gambia, The  Njabakunda   
31  AG0085-C              2521  Martin Donnelly  Gambia, The  Njabakunda   
32  AG0096-C              2532  Martin Donnelly  Gambia, The  Njabakunda   
33  AG0126-C              2562  Martin Donnelly  Gambia, The  Njabakunda   
34  AG0152-C              2619  Martin Donnelly  Gambia, The  Njabakunda   
35  AG0183-C              2681  Martin Donnelly  Gambia, The  Njabakunda   
36  AG0127-C              2563  Martin Donnelly  Gambia, The  Njabakunda   
37  AG0144-C              2611  Martin Donnelly  Gambia, The  Njabakunda   
38  AG0156-C              2623  Martin Donnelly  Gambia, The  Njabakunda   
39  AG0082-C              2518  Martin Donnelly  Gambia, The  Njabakunda   
40  AG0097-C              2533  Martin Donnelly  Gambia, The  Njabakunda   
41  AG0100-C              2536  Martin Donnelly  Gambia, The  Njabakunda   
42  AG0109-C              2545  Martin Donnelly  Gambia, The  Njabakunda   
43  AG0124-C              2560  Martin Donnelly  Gambia, The  Njabakunda   
44  AG0142-C              2609  Martin Donnelly  Gambia, The  Njabakunda   
45  AG0146-C              2613  Martin Donnelly  Gambia, The  Njabakunda   
46  AG0169-C              2636  Martin Donnelly  Gambia, The  Njabakunda   
47  AG0178-C              2676  Martin Donnelly  Gambia, The  Njabakunda   
48  AG0195-C              2693  Martin Donnelly  Gambia, The  Njabakunda   
49  AG0089-C              2525  Martin Donnelly  Gambia, The  Njabakunda   
50  AG0111-C              2547  Martin Donnelly  Gambia, The  Njabakunda   
51  AG0125-C              2561  Martin Donnelly  Ga

In [7]:
# Determine collection dates.

df_collection_dates = (
    df_samples
    .groupby(["year", "month"])
    .size()
    .reset_index()
    .rename(columns={0: 'count'})
)
df_collection_dates

year  month  count
0  2011      8     44
1  2011      9      8

In [8]:
# Determine first and last collection months.

min_month = df_collection_dates["month"].min()
max_month = df_collection_dates["month"].max()

if min_month < 0:
    start_month = end_month = None
else:
    start_month = pd.to_datetime(min_month, format="%m").month_name()
    end_month = pd.to_datetime(max_month, format="%m").month_name()
    
start_month, end_month

('August', 'September')

In [9]:
# Determine unique collection locations.

df_locations = df_samples[["location", "longitude", "latitude"]].drop_duplicates()
df_locations

location  longitude  latitude
0  Njabakunda      -15.9     13.55

In [10]:
# Extract provenance information about the samples.

df_contributors = df_samples[["release", "sample_set", "contributor"]].drop_duplicates()
df_contributors["study"] = df_contributors.apply(
    lambda v: "Ag1000G" if v["sample_set"].startswith("AG1000G") else "TODO",
    axis="columns"
)
df_contributors["release"] = df_contributors["release"].apply(
    lambda v: f"Ag{v}"
)
df_contributors.rename(columns={
    "contributor": "Contributor",
    "study": "Study",
    "release": "Data release",
    "sample_set": "Sample set",
}, inplace=True)
df_contributors.set_index(["Contributor", "Study", "Data release"], inplace=True)
df_contributors

Sample set
Contributor     Study   Data release              
Martin Donnelly Ag1000G Ag3.0         AG1000G-GM-A

In [11]:
# Build a paragraph with summary information about the samples in this cohort.

n_locations = len(df_locations)

summary_info = f"""This cohort comprises {cohort['cohort_size']:,} samples from the 
*{cohort['taxon']}* taxon, collected from {n_locations} locations within the administrative 
division of {cohort['admin2_name']}, {cohort['admin1_name']}, {cohort['country']}."""

if start_month and start_month == end_month:
    summary_info += f""" Collections were made in {start_month} {cohort['year']}."""
elif start_month:
    summary_info += f""" Collections were made between {start_month} and {end_month} in {cohort['year']}."""
else:
    summary_info += f""" Collections were made in {cohort['year']}."""
    
display(Markdown(summary_info))


This cohort comprises 52 samples from the 
*gcx1* taxon, collected from 1 locations within the administrative 
division of Central Badibu, Kerewan, Gambia, The. Collections were made between August and September in 2011.

## Selection scans

In [12]:
# load signals to overlay on H12 plots
import pandas as pd

df_signals_contigs = []
for contig in contigs:

    try:
        df_signals_contig = pd.read_csv(here() / "build/h12-signal-detection/" / f"{cohort_id}_{contig}.csv")
    except pd.errors.EmptyDataError:
        df_signals_contig = pd.DataFrame()
    df_signals_contigs.append(df_signals_contig)  
    
df_signals = pd.concat(df_signals_contigs)

# Add extra columns to help with overlaying signals on plots.
df_signals["bottom"] = 0
df_signals["top"] = 1

df_signals

cohort_id contig     gcenter   pcenter  delta_i  \
0  GM-N_Central-Baddibu_gcx1_2011_Q3    2RL   56.945621  28472811     3511   
1  GM-N_Central-Baddibu_gcx1_2011_Q3    2RL   96.150959  48075480     1157   
2  GM-N_Central-Baddibu_gcx1_2011_Q3    2RL  138.068274  72804768     1208   
3  GM-N_Central-Baddibu_gcx1_2011_Q3    2RL  158.140965  82841114     1011   
0  GM-N_Central-Baddibu_gcx1_2011_Q3    3RL    1.000856    500429     1512   
1  GM-N_Central-Baddibu_gcx1_2011_Q3    3RL   51.548683  25774342     1758   
2  GM-N_Central-Baddibu_gcx1_2011_Q3    3RL   64.067901  32033951     1372   

   stat_max    gpos_max  ppos_max  focus_gstart  focus_gstop  ...      skew  \
0    0.6924   56.969424  28484712     56.731402    57.285684  ... -0.333355   
1    0.2372   96.164356  48082178     96.017990    96.217444  ...  0.500000   
2    0.3810  138.068274  72804768    138.034454   138.098165  ...  0.089065   
3    0.3182  158.073442  82807352    157.970845   158.226026  ...  0.500000   
0    0.1954    0.033504     16752      0.653052     1.174759  ...  0.500000   
1    0.2172   51.766086  25883043     51.509244    51.627563  ... -0.500000   
2    0.2898   64.064066  32032033     64.045799    64.112104  ... -0.500000   

   decay_left  decay_right  baseline           aic           bic       rss  \
0    0.856878     1.360250  0.081572 -12422.340910 -12394.200755  4.846371   
1    0.531878     0.265939  0.068392 -11951.738710 -11925.080135  0.608567   
2    0.135277     0.119565  0.081996 -13720.335322 -13692.712516  1.121620   
3    0.680481     0.340241  0.071317 -13259.247144 -13231.546693  1.631469   
0    1.391219     0.695609  0.030999 -11777.325249 -11751.022636  0.359547   
1    0.157759     0.315517  0.038229 -16243.008178 -16215.226038  0.390762   
2    0.088407     0.176815  0.047474 -12793.343976 -12766.464566  0.526639   

   constant_aic  bottom  top  
0  -8910.705765       0    1  
1 -10793.947989       0    1  
2 -12511.393414       0    1  
3 -12248.239320       0    1  
0 -10264.403183       0    1  
1 -14484.279134       0    1  
2 -11421.271280       0    1  

[7 rows x 32 columns]

In [13]:
# load window sizes 
h12_calibration_dir = "build/h12-calibration"
with open(here() / h12_calibration_dir / f"{cohort_id}.yaml") as h12_calibration_file:
    h12_calibration_params = yaml.safe_load(h12_calibration_file)
h12_window_size = h12_calibration_params["h12_window_size"]
g123_calibration_dir = "build/g123-calibration"
with open(here() / g123_calibration_dir / f"{cohort_id}.yaml") as g123_calibration_file:
    g123_calibration_params = yaml.safe_load(g123_calibration_file)
g123_window_size = g123_calibration_params["g123_window_size"]

if cohort.taxon == 'arabiensis':
    phasing_analysis = 'arab'
else:
    phasing_analysis = 'gamb_colu'

ihs_window_size = 100

def plot_h12_g123_ihs_tracks(
        contig, 
        df_signals,
        sizing_mode='stretch_width', 
        show=False, 
        width=800, 
        track_height=150,
        genes_height=90,
    ):

    sample_query = cohort["sample_query"]
    
    fig1 = ag3.plot_h12_gwss_track(
        contig=contig, 
        window_size=h12_window_size, 
        analysis=phasing_analysis, 
        sample_sets=sample_sets,
        sample_query=sample_query, 
        min_cohort_size=min_cohort_size,
        max_cohort_size=max_cohort_size,
        sizing_mode=sizing_mode,
        show=show,
        width=width,
        height=track_height,
    )
    fig1.xaxis.visible = False
        
    if not df_signals.empty:
        df = df_signals.query("contig == @contig")
        center_xs = [np.array([row.pcenter, row.pcenter]) for idx, row in df.iterrows()]
        center_ys = [np.array([0, 1]) for idx, row in df.iterrows()]
        source = bkmod.ColumnDataSource(data={
            'cohort': df.cohort_id,
            'chromosome': df.contig,
            'score': df.delta_i.astype(int),
            'peak_start': df.span2_pstart,
            'peak_stop': df.span2_pstop,
            'focus_start': df.focus_pstart,
            'focus_stop': df.focus_pstop,    
            'center_xs': center_xs,
            'center_ys': center_ys,
            'bottom': df.bottom ,
            'top': df.top,
            })
        quad = fig1.quad(bottom='bottom', top='top', left='peak_start', right='peak_stop', 
              source=source, color="gray", alpha=.1, line_width=1)
        quad2 = fig1.quad(bottom='bottom', top='top', left='focus_start', right='focus_stop', 
              source=source, color="red", alpha=.4)
        glyph = bkmod.MultiLine(xs='center_xs', ys='center_ys', line_color='red', line_width=2, line_alpha=0.8)
        fig1.add_glyph(source, glyph)
    
        hover = bkmod.HoverTool(tooltips=[
            ("Cohort", '@cohort'),
            ("Score", '@score'),
            ("Focus", "@focus_start{,} - @focus_stop{,}"),
        ], renderers=[quad])

        fig1.add_tools(hover)
    
    fig2 = ag3.plot_g123_gwss_track(
        contig=contig, 
        window_size=g123_window_size, 
        sites=phasing_analysis,
        site_mask=phasing_analysis, 
        sample_sets=sample_sets,
        sample_query=sample_query, 
        min_cohort_size=min_cohort_size,
        max_cohort_size=max_cohort_size,
        sizing_mode=sizing_mode,
        width=width,
        height=track_height,
        show=show,
        title="",
        x_range=fig1.x_range,
    )
    fig2.xaxis.visible = False

    fig3 = ag3.plot_ihs_gwss_track(
        contig=contig, 
        window_size=ihs_window_size, 
        analysis=phasing_analysis, 
        sample_sets=sample_sets,
        sample_query=sample_query, 
        min_cohort_size=min_cohort_size,
        max_cohort_size=max_cohort_size,
        sizing_mode=sizing_mode,
        width=width,
        height=track_height,
        show=show,
        title="",
        x_range=fig1.x_range,
    )
    fig3.xaxis.visible = False


    fig4 = ag3.plot_genes(
        region=contig, 
        show=show,
        sizing_mode=sizing_mode,
        width=width,
        height=genes_height,
        x_range=fig1.x_range
        )
                        
    fig = bklay.gridplot(
        [fig1, fig2, fig3, fig4],
        ncols=1,
        toolbar_location="above",
        merge_tools=True,
        sizing_mode=sizing_mode,
    )
    return fig 

In [14]:
for contig in contigs:
    
    display(HTML(f"<h3>Chromosome {contig}</h3>"))
    
    fig = plot_h12_g123_ihs_tracks(
        contig=contig,
        df_signals=df_signals,
    );

    bkplt.show(fig)


## Sampling information

In [15]:
from ipyleaflet import Map, Marker, basemaps
from ipywidgets import HTML

center = cohort[['latitude', 'longitude']].to_list()
m = Map(center=center, zoom=9, basemap=basemaps.OpenTopoMap)

df = df_samples[['latitude', 'longitude', 'taxon']].groupby(['latitude', 'longitude', 'taxon']).size().to_frame().rename(columns={0: 'count'}).reset_index()

for coh_id, row in df.iterrows():
    lat, long = row[['latitude', 'longitude']]
    
    if row['taxon'] == 'gambiae':
        color= 'red'
    elif row['taxon'] == 'coluzzii':
        color='cadetblue'
    elif row['taxon'] == 'arabiensis':
        color='lightgreen'
    else: 
        color='gray'

    marker = Marker(location=(lat, long), draggable=True, opacity=0.7, color=color)
    m.add_layer(marker);

    message2 = HTML()
    message2.value = f"n = {row['count']}"
    marker.popup = message2

display(m)

Map(center=[13.55, -15.9], controls=(ZoomControl(options=['position', 'zoom_in_text', 'zoom_in_title', 'zoom_o…

In [16]:

if min_month >= 0:
    # For this cohort we have month data, so show a breakdown of sample
    # numbers by location and month.
    
    # Construct a pivot table counting samples.
    df_loc_dt = df_samples.pivot_table(
        index=["location", "longitude", "latitude"],
        columns="month",
        values="sample_id",
        aggfunc="count",
        fill_value=0,
    )

    # Tidy up the columns using a multi index.
    df_loc_dt.reset_index(inplace=True)
    cols = pd.MultiIndex.from_tuples(
        [("Location", "Name"), ("Location", "Longitude"), ("Location", "Latitude")] + 
        [("Date", pd.to_datetime(x, format="%m").month_name()) 
         for x in df_loc_dt.columns[3:]], 
    )
    df_loc_dt.columns = cols
    
else:
    # For this cohort we do not have month data, so show a breakdown of sample
    # numbers by location only.
    
    # Construct a pivot table counting samples.
    df_loc_dt = df_samples.groupby(["location", "longitude", "latitude"]).agg({"sample_id": "count"})

    # Tidy up the columns using a multi index.
    df_loc_dt.reset_index(inplace=True)
    cols = pd.MultiIndex.from_tuples(
        [("Location", "Name"), ("Location", "Longitude"), ("Location", "Latitude"), ("Date", cohort.year)]
    )
    df_loc_dt.columns = cols

# Style the table.
df_loc_dt_styled = (
    df_loc_dt
    .style
    .format(precision=3)
    .set_caption("Number of samples collected.")
    .hide()
)
display(df_loc_dt_styled)    

## Diagnostics
### H12 calibration

In [17]:
display(Markdown(f"Selected window size: **{h12_window_size:,}**"))

window_sizes = (100, 200, 500, 1000, 2000, 5000, 10000, 20000)

ag3.plot_h12_calibration(
    contig=h12_calibration_contig,
    analysis=phasing_analysis,
    sample_sets=sample_sets,
    sample_query=cohort['sample_query'],
    min_cohort_size=min_cohort_size,
    max_cohort_size=max_cohort_size,
    window_sizes=window_sizes,
);


Selected window size: **1,000**

### G123 Calibration

In [18]:
display(Markdown(f"Selected window size: **{g123_window_size:,}**"))

ag3.plot_g123_calibration(
    contig=h12_calibration_contig,
    sites=phasing_analysis,
    site_mask=phasing_analysis,
    sample_sets=sample_sets,
    sample_query=cohort['sample_query'],
    min_cohort_size=min_cohort_size,
    max_cohort_size=max_cohort_size,
    window_sizes=window_sizes,
);

Selected window size: **500**

## Data sources

In [19]:
df_sources_style = (
    df_contributors
    .style
    .set_caption("MalariaGEN Vector Observatory partners, studies and sample sets contributing data for this cohort.")
)
df_sources_style